In [1]:
from scipy.io import loadmat
from ssmlearnpy import SSMLearn
from ssmlearnpy.reduced_dynamics.advector import advect
import numpy as np
import plotly.graph_objects as go
from mpl_toolkits import mplot3d

mat = loadmat('data.mat')
n_traj = len(mat['PODTraj'])
idx_train = [0, 2, 4, 5, 7, 8]
idx_test = [1, 3, 6]
n_traj_train, n_traj_test = len(idx_train), len(idx_test)

t_train = [mat['PODTraj'][i][0].flatten() for i in idx_train]
x_full_train = [mat['PODTraj'][i][1] for i in idx_train]
x_reduced_train = [mat['PODTraj'][i][1][:2,:] for i in idx_train]

n_traj_test = len(mat['PODTraj'])-n_traj_train
t_test = [mat['PODTraj'][i][0].flatten() for i in idx_test]
x_full_test = [mat['PODTraj'][i][1] for i in idx_test]
x_reduced_test = [mat['PODTraj'][i][1][:2,:] for i in idx_test]

ssm = SSMLearn(
    t = t_train, 
    x = x_full_train, 
    reduced_coordinates = x_reduced_train,
    ssm_dim=2, 
    dynamics_type = 'flow',
    label_observables = 'POD',
    label_reduced_coordinates = 'POD'
)

In [2]:
fig = ssm.plot()
fig.show()

In [3]:
fig = ssm.plot(data_name = 'reduced_coordinates', idx_coordinates=[1, 2])
fig.show()

In [4]:
ssm.get_parametrization(poly_degree=18)    
ssm.get_reduced_dynamics(poly_degree=11) 
ssm.predict()  

INFO   2022-10-05 18:24:26 ridge Transforming data
INFO   2022-10-05 18:24:26 ridge Skipping CV on ridge regression
INFO   2022-10-05 18:24:26 ridge Fitting regression model
INFO   2022-10-05 18:24:27 ridge Transforming data
INFO   2022-10-05 18:24:27 ridge Skipping CV on ridge regression
INFO   2022-10-05 18:24:27 ridge Fitting regression model


In [9]:
fig = ssm.plot(data_name = 'reduced_coordinates', idx_trajectories=[1, 5], with_predictions = True)
fig.show()
fig = ssm.plot(data_name = 'reduced_coordinates', idx_trajectories=[1, 5], idx_coordinates=[1, 2], with_predictions = True)
fig.show()
fig = ssm.plot(data_name = 'observables', idx_trajectories=[1, 5], idx_coordinates=[3], with_predictions = True)
fig.show()

In [10]:
fig = ssm.plot(data_name = 'observables', type_predictions='geometry', data_type='errors')
fig.show()

fig = ssm.plot(data_name = 'reduced_coordinates', data_type='errors')
fig.show()

fig = ssm.plot(data_name = 'observables', data_type='errors')
fig.show()

In [ ]:
fig = ssm.plot(data_name = 'observables', idx_trajectories=[1, 5], idx_coordinates=[1, 2, 3], with_predictions = True)
fig.show()

In [22]:

fig = go.Figure()

r_vec = np.linspace(0, 25, 101)
th_vec = np.linspace(0, 2*np.pi, 101)
r_mesh, th_mesh = np.meshgrid(r_vec,th_vec)
x_mesh, y_mesh = r_mesh*np.cos(th_mesh), r_mesh*np.sin(th_mesh)
x_reduced_surf = np.array([x_mesh.flatten(), y_mesh.flatten(),])

x_full_surf = ssm.decoder.predict(x_reduced_surf.T).T
n_coord = 3
z_vec = x_full_surf[n_coord,:]
z_mesh = z_vec.reshape(x_mesh.shape)
surf_coloring = r_mesh/np.amax(r_mesh)
line_marker = dict(color='black', width=2)
fig.add_surface(
    x=x_mesh,
    y=y_mesh,
    z=z_mesh,
    surfacecolor=np.square(surf_coloring),
    opacity = 0.7,
    colorscale='agsunset',
    showscale=False,
    showlegend=False
)
for i_traj in (1,4):
    fig.add_scatter3d(
        x=x_reduced_train[i_traj][0,:], 
        y=x_reduced_train[i_traj][1,:], 
        z=x_full_train[i_traj][n_coord,:],
        mode='lines', 
        line=line_marker, 
        name='',
        showlegend=False
    )
plt_width = 560  
plt_height = 420
plt_margins = plt_width / 20
fig.update_layout(title='SSM', autosize=True,
                  width=plt_width, height=plt_height,
                  margin=dict(l=plt_margins, r=plt_margins, b=plt_margins, t=plt_margins), 
                  scene = dict(
                    xaxis_title='POD<sub>1</sub>',
                    yaxis_title='POD<sub>2</sub>',
                    zaxis_title='POD<sub>3</sub>'),
                  font_family='Helvetica',
                  font_color='black'
)
fig.show()


In [16]:
test_predictions = ssm.predict(t = t_test, x = x_full_test, x_reduced = x_reduced_test)  
e_predict = test_predictions['errors']

plt_coord = 1
fig = ssm.plot(
        t = t_test,
        x = x_reduced_test,
        t_pred = test_predictions['time'],
        x_pred = test_predictions['reduced_coordinates'],
        with_predictions = True, idx_coordinates=[plt_coord], plt_labels = ['time [s]', 'POD']
    )
fig.show()
fig = ssm.plot(
        t = t_test,
        x = x_reduced_test,
        t_pred = test_predictions['time'],
        x_pred = test_predictions['reduced_coordinates'],
        with_predictions = True, idx_coordinates=[1, 2], plt_labels = ['POD', 'POD']
    )
fig.show()
plt_coord = 3
fig = ssm.plot(
        t = t_test,
        x = x_full_test,
        t_pred = test_predictions['time'],
        x_pred = test_predictions['observables'],
        with_predictions = True, idx_coordinates=[plt_coord], plt_labels = ['time [s]', 'POD']
    )
fig.show()

fig = ssm.plot(
        t = test_predictions['time'],
        x = test_predictions['errors'],
        plt_labels = ['time [s]', 'Errors [%]'])
fig.show()